# Set up imports

In [30]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [31]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [32]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [33]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [34]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [35]:
data = df.abstract.values.tolist()

In [36]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [37]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [38]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [39]:
# filter words that occur in more than 90% of documents
id2word.filter_extremes(no_above = 0.980)
print(id2word)

Dictionary(4415 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [40]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [41]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [42]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [43]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [44]:
ldaseq.print_topic_times(topic=0)# evolution of 1st topic through all timeslices

[[('algorithm', 0.02001464270775592),
  ('graph', 0.01805876934958685),
  ('distribution', 0.015127591707404991),
  ('clustering', 0.010382493262139872),
  ('problem', 0.009714484416516098),
  ('random', 0.009074106351936962),
  ('show', 0.008883620617766503),
  ('bound', 0.00790771978262156),
  ('model', 0.00707601708058537),
  ('sample', 0.007038706668208582),
  ('result', 0.006698439716302123),
  ('probability', 0.0063315100290742),
  ('cluster', 0.006034058497477223),
  ('estimator', 0.005914149305634344),
  ('number', 0.00568866745628345),
  ('estimate', 0.005599483105679303),
  ('estimation', 0.005471453021931006),
  ('function', 0.005391876913733555),
  ('based', 0.004958469470331926),
  ('density', 0.0048312708442107815)],
 [('algorithm', 0.020072305384267956),
  ('graph', 0.01810852672424559),
  ('distribution', 0.015166493049635297),
  ('clustering', 0.01040435375275951),
  ('problem', 0.0097350764533281),
  ('random', 0.009092775797164665),
  ('show', 0.00890181854527311),
 

In [45]:
ldaseq.print_topic_times(topic=1)

[[('algorithm', 0.02856612756205004),
  ('learning', 0.021135512499351555),
  ('bound', 0.01785583367962691),
  ('problem', 0.015680172051880093),
  ('online', 0.012536830484486072),
  ('regret', 0.009573747519004798),
  ('show', 0.00895620766920906),
  ('decision', 0.00845892020978875),
  ('action', 0.00818348836753627),
  ('policy', 0.00791635136458241),
  ('setting', 0.007822445928862087),
  ('state', 0.007757814474793638),
  ('reward', 0.006979173753863453),
  ('optimal', 0.006823911247819168),
  ('result', 0.006785116318822765),
  ('case', 0.006654764400421834),
  ('game', 0.0063288231497841884),
  ('agent', 0.0062045393315025),
  ('complexity', 0.006095143409196123),
  ('time', 0.005920394753925744)],
 [('algorithm', 0.028651466994816497),
  ('learning', 0.021192349252194227),
  ('bound', 0.017900535380095988),
  ('problem', 0.015717897685142174),
  ('online', 0.012564189216716468),
  ('regret', 0.009592110841036798),
  ('show', 0.008972836145422798),
  ('decision', 0.00847400633

In [46]:
ldaseq.print_topic_times(topic=2)

[[('model', 0.022028667415012863),
  ('data', 0.011350114145475567),
  ('neural', 0.009644274773831396),
  ('neuron', 0.009306890832481669),
  ('stimulus', 0.007188428447909178),
  ('method', 0.007056694404849539),
  ('time', 0.006916581901159518),
  ('process', 0.0068208212400564065),
  ('activity', 0.006700711698096829),
  ('dynamic', 0.006538075338020769),
  ('system', 0.006510838937463349),
  ('show', 0.006364357710499983),
  ('network', 0.0063448149610437965),
  ('spike', 0.006150631874874854),
  ('brain', 0.006107659992262622),
  ('response', 0.00600953814882614),
  ('information', 0.005343068890582459),
  ('gaussian', 0.00513198135726001),
  ('using', 0.005121616719413987),
  ('signal', 0.005010546708868364)],
 [('model', 0.02209664536567402),
  ('data', 0.011392729931543307),
  ('neural', 0.009629834756991813),
  ('neuron', 0.009336416493600848),
  ('stimulus', 0.007208548373564037),
  ('method', 0.0070763608434542),
  ('time', 0.006918518192731392),
  ('process', 0.00682614411

In [47]:
ldaseq.print_topic_times(topic=3)

[[('learning', 0.03748305008420158),
  ('kernel', 0.02339581755985706),
  ('data', 0.019819606711529585),
  ('classification', 0.01691033195784717),
  ('feature', 0.015692902408596065),
  ('method', 0.014778941781822548),
  ('task', 0.014570768868996598),
  ('classifier', 0.011610602397433528),
  ('problem', 0.011107504285015269),
  ('training', 0.011015445318626806),
  ('approach', 0.01088201569909852),
  ('label', 0.010336742677594869),
  ('algorithm', 0.01019201145605707),
  ('set', 0.008614102320045862),
  ('prediction', 0.007528920155729323),
  ('class', 0.007100383494967685),
  ('show', 0.007070745296501966),
  ('loss', 0.006959722599283049),
  ('framework', 0.006571294902773406),
  ('performance', 0.006549429139913056)],
 [('learning', 0.037593083655126244),
  ('kernel', 0.023453021288658667),
  ('data', 0.019864463469606755),
  ('classification', 0.016945990784781755),
  ('feature', 0.015725057085761197),
  ('method', 0.01480780330635856),
  ('task', 0.014599872834406774),
  ('

In [48]:
ldaseq.print_topic_times(topic=4)

[[('network', 0.037384688233866564),
  ('learning', 0.016804036541980986),
  ('neural', 0.013956926029828924),
  ('deep', 0.013542234599794423),
  ('model', 0.013220339511688108),
  ('training', 0.012490776748582073),
  ('input', 0.011278732236234495),
  ('layer', 0.010260727445270845),
  ('feature', 0.009630831397729541),
  ('task', 0.009513061187553518),
  ('architecture', 0.008906399149440658),
  ('representation', 0.008090684823813187),
  ('show', 0.007788772624077153),
  ('image', 0.0076275662420468935),
  ('performance', 0.0072996363104163055),
  ('convolutional', 0.00677565146483294),
  ('memory', 0.00673461721999924),
  ('result', 0.006549754244354585),
  ('sequence', 0.0062243422333606154),
  ('using', 0.006152482880476003)],
 [('network', 0.03722429314997404),
  ('learning', 0.016862337277485377),
  ('neural', 0.01383816583790455),
  ('deep', 0.013629936470650708),
  ('model', 0.013234374020091507),
  ('training', 0.012508948180181225),
  ('input', 0.011159061448494203),
  ('

In [49]:
ldaseq.print_topic_times(topic=5)

[[('problem', 0.021775974986230667),
  ('matrix', 0.01785330840348505),
  ('sparse', 0.01778422638113923),
  ('algorithm', 0.014994180157434396),
  ('regression', 0.013580254839979447),
  ('method', 0.01349606615483091),
  ('convex', 0.00934693723255414),
  ('linear', 0.008840200023690925),
  ('analysis', 0.008068623694815197),
  ('data', 0.00788834931013895),
  ('regularization', 0.007546256403885616),
  ('result', 0.007412566029420458),
  ('norm', 0.006919709985355463),
  ('show', 0.006848866474242633),
  ('sparsity', 0.006333568251527675),
  ('estimation', 0.005921991216890078),
  ('paper', 0.005818818262854142),
  ('optimization', 0.0055913667498653),
  ('vector', 0.0053436813095968615),
  ('model', 0.0052699405677999476)],
 [('problem', 0.021846906250811687),
  ('matrix', 0.017906690178966747),
  ('sparse', 0.017836915232819432),
  ('algorithm', 0.014965530886297429),
  ('regression', 0.0136147960955899),
  ('method', 0.013531607400968947),
  ('convex', 0.009366161585257287),
  ('

In [50]:
ldaseq.print_topic_times(topic=6)

[[('image', 0.029848210138898566),
  ('model', 0.02016807781204952),
  ('object', 0.019323684651213546),
  ('human', 0.013950422487696436),
  ('feature', 0.010515866694095275),
  ('visual', 0.010264324632242422),
  ('approach', 0.007502858304374293),
  ('task', 0.007189433012158601),
  ('scene', 0.00642745494392607),
  ('two', 0.006402605674300553),
  ('motion', 0.006117583645505266),
  ('information', 0.005358942104405947),
  ('recognition', 0.005343698460842106),
  ('using', 0.005337017412406732),
  ('experiment', 0.005251514786112206),
  ('show', 0.005172788893954723),
  ('problem', 0.005121843317563039),
  ('result', 0.004927717675540259),
  ('system', 0.004775292992844652),
  ('detection', 0.004733263200314449)],
 [('image', 0.02982119340324013),
  ('model', 0.02027341201206684),
  ('object', 0.01932744118407966),
  ('human', 0.014007840675049439),
  ('feature', 0.010551577918958582),
  ('visual', 0.010299342710253618),
  ('approach', 0.007523093367313439),
  ('task', 0.0072082324

In [51]:
ldaseq.print_topic_times(topic=7)

[[('model', 0.06853851259593344),
  ('inference', 0.024116400984499214),
  ('data', 0.017488492804212698),
  ('latent', 0.0156900460428657),
  ('bayesian', 0.013794629886306198),
  ('distribution', 0.013027804493039289),
  ('method', 0.011331844447632843),
  ('structure', 0.011285170946836814),
  ('variable', 0.01124483355029102),
  ('approach', 0.011219448829146005),
  ('process', 0.011008631700857745),
  ('probabilistic', 0.010923903161278921),
  ('learning', 0.010176226790908441),
  ('prior', 0.009213001708425522),
  ('topic', 0.008790615970095438),
  ('variational', 0.008062751247705644),
  ('mixture', 0.007858976738131334),
  ('word', 0.007840439629784651),
  ('document', 0.007006026684073464),
  ('posterior', 0.006982544076043838)],
 [('model', 0.06850278730915157),
  ('inference', 0.02420308160738688),
  ('data', 0.017539141088559564),
  ('latent', 0.01573461788366158),
  ('bayesian', 0.013829923552385392),
  ('distribution', 0.013060243741069521),
  ('method', 0.011357807848004

In [52]:
ldaseq.print_topic_times(topic=8)

[[('data', 0.038562662713415435),
  ('metric', 0.015233955181529967),
  ('distance', 0.011874518039232045),
  ('method', 0.01170829527306954),
  ('space', 0.011252463209383107),
  ('problem', 0.011022178886925844),
  ('similarity', 0.010931855647319553),
  ('learning', 0.010505364045144858),
  ('point', 0.010143680268627485),
  ('algorithm', 0.009087613474767891),
  ('manifold', 0.008537080865795915),
  ('local', 0.00775660824796751),
  ('dimensionality', 0.007674861379262789),
  ('structure', 0.007449930787950077),
  ('function', 0.0073940975786743),
  ('measure', 0.007279695975088476),
  ('dimension', 0.007210879585670158),
  ('set', 0.006933461613365222),
  ('show', 0.006815898046244049),
  ('using', 0.006679933000417669)],
 [('data', 0.038680596025112556),
  ('metric', 0.015265950574725864),
  ('distance', 0.011896699974695982),
  ('method', 0.01172947387718436),
  ('space', 0.011272331372976195),
  ('problem', 0.011041797630797491),
  ('similarity', 0.010951337004073972),
  ('lear

In [53]:
ldaseq.print_topic_times(topic=9)

[[('algorithm', 0.037619087115734716),
  ('method', 0.027493331672210047),
  ('function', 0.024163098565435488),
  ('problem', 0.017475758723064106),
  ('learning', 0.012900044747868855),
  ('gradient', 0.012779224660757791),
  ('optimization', 0.011251913281706985),
  ('approach', 0.010818794040602734),
  ('show', 0.00902703333904097),
  ('approximation', 0.008087063114798265),
  ('convergence', 0.0079766115669706),
  ('stochastic', 0.007333768115329297),
  ('paper', 0.00667311115353984),
  ('solution', 0.006158536479605652),
  ('policy', 0.0061355484361187386),
  ('search', 0.006086165706212381),
  ('result', 0.005820008345532306),
  ('descent', 0.005500651552689332),
  ('objective', 0.005185327893194032),
  ('using', 0.005094752340206989)],
 [('algorithm', 0.037734505856323694),
  ('method', 0.027572545391149915),
  ('function', 0.02422805684316426),
  ('problem', 0.01751637001224952),
  ('learning', 0.012925699787037155),
  ('gradient', 0.012804794644392884),
  ('optimization', 0.0

In [54]:

# to check Document - Topic proportions, use `doc-topics`
doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
print (doc)
# this document is made up of different topics like this

[2.49292958e-01 2.12314225e-04 1.89952270e-01 2.12314225e-04
 2.12314225e-04 2.12314225e-04 5.20689865e-02 5.07411900e-01
 2.12314225e-04 2.12314225e-04]


In [55]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [56]:
ldaseq.print_topic_times(1) # evolution of values for all time slice for topic 2


[[('algorithm', 0.02856612756205004),
  ('learning', 0.021135512499351555),
  ('bound', 0.01785583367962691),
  ('problem', 0.015680172051880093),
  ('online', 0.012536830484486072),
  ('regret', 0.009573747519004798),
  ('show', 0.00895620766920906),
  ('decision', 0.00845892020978875),
  ('action', 0.00818348836753627),
  ('policy', 0.00791635136458241),
  ('setting', 0.007822445928862087),
  ('state', 0.007757814474793638),
  ('reward', 0.006979173753863453),
  ('optimal', 0.006823911247819168),
  ('result', 0.006785116318822765),
  ('case', 0.006654764400421834),
  ('game', 0.0063288231497841884),
  ('agent', 0.0062045393315025),
  ('complexity', 0.006095143409196123),
  ('time', 0.005920394753925744)],
 [('algorithm', 0.028651466994816497),
  ('learning', 0.021192349252194227),
  ('bound', 0.017900535380095988),
  ('problem', 0.015717897685142174),
  ('online', 0.012564189216716468),
  ('regret', 0.009592110841036798),
  ('show', 0.008972836145422798),
  ('decision', 0.00847400633

In [57]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.8278030402019803
CV1 0.4258654403043834
U_Mass2 -1.8270933017261917
CV2 0.4258654403043834
U_Mass3 -1.7942458209455174
CV3 0.42396348103308484
U_Mass4 -1.8472365861721922
CV4 0.42367783347759325
U_Mass5 -1.8378448841059645
CV5 0.4254507242180325
U_Mass6 -1.8313727377798148
CV6 0.42646363984208674
U_Mass7 -1.8558534676405993
CV7 0.43614974002240575
U_Mass8 -1.8688088792661754
CV8 0.43638670069910673
U_Mass9 -1.8915436445424416
CV9 0.4303651486043618
U_Mass10 -1.830758541560601
CV10 0.4298945210065588
U_Mass11 -1.7970181665569633
CV11 0.4293525333194127
U_Mass12 -1.7693121355523682
CV12 0.42452752029834856


In [58]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/